# Speech understanding
## 1. Introduction
This notebook is for playing with audio files. Understanding the fundamental speech frequency and other well known terms in Automatic Speech Recognition (ASR) like Mel-Frequency Cepstral Coefficients (MFCCs), Gammatone-Frequency Cepstral Coefficients (GFCC), Bark-Frequency Cepstral Coefficients (BFCC) and so on.
## 2. Audio import and playing audio

In [1]:
%matplotlib widget

import os
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

from copy import deepcopy


from IPython.display import display as iDisplay
from IPython.display import Audio as iAudio
from scipy.signal import decimate
from scipy.signal import spectrogram
from scipy.signal import istft
from scipy.signal import get_window

import audioread
import librosa
import librosa.core as audio
import seaborn as sns
from librosa.display import specshow, waveplot
from pydub import AudioSegment, effects

sns.set()

audio_book_path = r'./input/cienmejorespoesias_000_menendezypelayo_64kb.mp3'
noise_path = r'./input/city4_short.mp3'

class AudioManager:
    def __init__(self, path=''):
        self.path = path
        self.raw  = None
        self.norm = None
        self.ext = os.path.splitext(self.path)[1][1:]
        self.samples = None
        self.n_channels  = None
        self.sample_rate = None
        self.duration    = None
        if not self.path == '':
            self.load()
            
    def __add__(self, audio_manager):
        ret_value = deepcopy(self)
        ret_value.raw = ret_value.raw.overlay(audio_manager.raw)
        ret_value.norm = effects.normalize(ret_value.raw)
        ret_value.get_samples()
        
        return ret_value
        
    def get_samples(self):
        self.samples = np.array(self.raw.get_array_of_samples(), dtype=np.float32)
        
    def load(self):
        with audioread.audio_open(self.path) as fId:
            self.n_channels  = fId.channels
            self.sample_rate = fId.samplerate
            self.duration    = fId.duration
        self.raw = AudioSegment.from_file(self.path, self.ext)
        if self.n_channels != 1:
            print('Audio ' + self.path + ' contains more than one channel. Converting to mono')
            self.raw = self.raw.set_channels(1)
            self.n_channels = 1
            self.sample_rate = int(self.sample_rate/2)
        self.norm = effects.normalize(self.raw)
        self.get_samples()
        #self.samples, sr = librosa.load(self.path)
        #print('LibRosa Sampling rate '+ str(sr) + '\n' +
        #      'AudioRead Sampling rate ' + str(self.sample_rate))
        
    def player(self):
        return self.raw
    
    def cut_audio(self, start_millis,end_millis):
        self.raw = self.raw[start_millis:end_millis]
        self.get_samples()
        self.duration = (end_millis - start_millis)/1000
        
    def plot_spectrogram(self, plot_type='log'):
        plt.close()
        plot_types = ['log','linear']
        if not plot_type in plot_types:
            raise Exception('Unknown plot_type: Allowed ' + str(plot_types))
        fig_handler = plt.figure(dpi= 80, facecolor='w', edgecolor='k')
        db_values = librosa.amplitude_to_db(np.abs(librosa.stft(self.samples,n_fft=2048)), ref=np.max)
        specshow(db_values, sr=self.sample_rate, y_axis=plot_type, cmap='magma')
        plt.colorbar(format='%+2.0f dB')
        plt.title(plot_type + '-frequency power spectrogram')
        fig_handler.canvas.layout.width = '500px'
        fig_handler.tight_layout()
        
    def plot_wave(self):
        plt.close()
        fig_handler = plt.figure(dpi= 80, facecolor='w', edgecolor='k')
        if len(self.samples) > 10**5:
            waveplot(self.samples[:int(10**5)], sr=self.sample_rate)
        else:
            waveplot(self.samples, sr=self.sample_rate)
        fig_handler.canvas.layout.width = '500px'
        fig_handler.tight_layout()
        

In [2]:
# Loaing audio book
audio_book = AudioManager(audio_book_path)

# Loaing and normalizing noise audio
noise = AudioManager(noise_path)

Audio ./input/city4_short.mp3 contains more than one channel. Converting to mono


### 2.1 Players

In [3]:
audio_book.player()

In [4]:
noise.player()

### 2.2 Cut audios to 10 secs duration

In [5]:
start_millis = 0
end_millis = 10*1000
audio_book.cut_audio(start_millis,end_millis)
noise.cut_audio(start_millis,end_millis)

In [6]:
audio_book.player()

In [7]:
noise.player()

### 2.3 Spectrograms

In [8]:
audio_book.plot_spectrogram('linear')

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [9]:
audio_book.plot_wave()

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [10]:
noise.plot_spectrogram('linear')

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [11]:
noise.plot_wave()

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

## 3. Audio combination

In [12]:
#noise.raw = noise.raw + 8
sum_audio = audio_book + noise
sum_audio.player()

In [13]:
sum_audio.plot_spectrogram('linear')

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [14]:
sum_audio.plot_wave()

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

## 4. Checking if spectrogram for noise signal is well calculated

In [15]:
import scipy
import numpy as np

plt.close()

# Generating a pure tone in centered in f0 with the same rate as the noise signal
seconds_duration = 5
time_sim = np.arange(0,seconds_duration,1/noise.sample_rate)
f0 = 5500
pure_tone = np.sin(2*np.pi*f0*time_sim)
plt.plot(pure_tone)

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [16]:
# Ploting FFT for chcking that the tone is centered in the targeted frequency
f, Pxx = scipy.signal.welch(pure_tone, fs = noise.sample_rate)
plt.plot(f,Pxx)

In [17]:
# Combining signals in time domain
input_signal = noise.samples
input_signal[0:len(pure_tone)] += 10*pure_tone

In [18]:
# Computing spectrogram with scipy and ploting with LibRosa
n_samples_window = 2048
freq, time, stft = scipy.signal.spectrogram(
    input_signal, fs=noise.sample_rate, 
    window=scipy.signal.get_window('hann', n_samples_window), 
    #nperseg=None, 
    noverlap=int(n_samples_window/2), nfft=n_samples_window, 
    #detrend='constant', 
    return_onesided=True, scaling='spectrum', axis=-1, mode='complex')

db_values = librosa.amplitude_to_db(np.abs(stft))
fig_handler = plt.figure(figsize=(10,10), dpi= 80, facecolor='w', edgecolor='k')
specshow(db_values, sr=noise.sample_rate, y_axis='linear',  cmap='magma')
fig_handler.tight_layout()
plt.colorbar(format='%+2.0f dB')
plt.title('linear' + '-frequency power spectrogram')

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

Text(0.5, 1, 'linear-frequency power spectrogram')

In the figure above the pure tone can e seen in 5.5KHz so noise signal has arround 5KHz badwith

In [19]:
# Take a look at frequency vector
delta_freq = freq[2]-freq[1]
print('Ten first components of frequency vector ' + str(freq[0:10]) + '\n' +
      'Delta_frequency: ' + str(delta_freq))
print('Spectrogram shape ' + str(stft.shape) + '\n' +
      'Time length ' + str(len(time)) + '\n'
      'Freq length ' + str(len(freq)))

Ten first components of frequency vector [ 0.         10.76660156 21.53320312 32.29980469 43.06640625 53.83300781
 64.59960938 75.36621094 86.1328125  96.89941406]
Delta_frequency: 10.7666015625
Spectrogram shape (1025, 429)
Time length 429
Freq length 1025


## 5. Downsampling audio
### 5.1 Half sampling rate

In [20]:
# Let's decimate input signal to half bandwitdh signal and check if audio book is still audible
factor = 2
print('Decimation factor: ' + str(factor))
decimated_audio_book = decimate(audio_book.samples, factor)
# Check the signal length that should be the half length
print('Old signal length: ' + str(len(audio_book.samples))+ '\n' +
      'New signal length: ' + str(len(decimated_audio_book)))

Decimation factor: 2
Old signal length: 220500
New signal length: 110250


In [21]:
# Plot the new spectrogram
n_samples_window = 1024
freq, time, stft = spectrogram(
    decimated_audio_book, fs=int(audio_book.sample_rate/factor), 
    window=get_window('hann', n_samples_window), 
    #nperseg=None, 
    noverlap=int(n_samples_window/2), nfft=n_samples_window, 
    #detrend='constant', 
    return_onesided=True, scaling='spectrum', axis=-1, mode='complex')
db_values = librosa.amplitude_to_db(stft)
#db_values = stft

fig_handler = plt.figure(dpi= 80, facecolor='w', edgecolor='k')
specshow(db_values, sr=int(audio_book.sample_rate/factor), y_axis='linear', cmap='magma')
fig_handler.tight_layout()
plt.colorbar(format='%+2.0f dB')
plt.title('linear' + '-frequency power spectrogram')

C:\ProgramData\Anaconda3\envs\base_cloned\lib\site-packages\librosa\core\spectrum.py:1702: UserWarning: amplitude_to_db was called on complex input so phase information will be discarded. To suppress this warning, call amplitude_to_db(np.abs(S)) instead.
  warnings.warn('amplitude_to_db was called on complex input so phase '


Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

Text(0.5, 1, 'linear-frequency power spectrogram')

In [22]:
iAudio(decimated_audio_book, rate=int(audio_book.sample_rate/factor))

In [23]:
# reconstruct signal from spectrogram
stft_recovered = librosa.db_to_amplitude(db_values)
data = istft(stft, fs=int(audio_book.sample_rate/factor), 
    window=get_window('hann', n_samples_window), 
    #nperseg=None, 
    noverlap=int(n_samples_window/2), nfft=n_samples_window)
iAudio(data, rate=int(audio_book.sample_rate/factor))

In [24]:
spectrum =  audio.stft(np.asfortranarray(decimated_audio_book),n_fft=1024,hop_length=int(1024/2),center=False)
recovered_data = audio.istft(spectrum, hop_length=int(1024/2))
iAudio(recovered_data, rate=int(audio_book.sample_rate/factor))

### 5.2 Quarter sampling rate

In [25]:
# Let's decimate input signal to half bandwitdh signal and check if audio book is still audible
factor = 4
print('Decimation factor: ' + str(factor))
decimated_audio_book = decimate(audio_book.samples, factor)
# Check the signal length that should be the half length
print('Old signal length: ' + str(len(audio_book.samples))+ '\n' +
      'New signal length: ' + str(len(decimated_audio_book)))

Decimation factor: 4
Old signal length: 220500
New signal length: 55125


In [26]:
# Plot the new spectrogram
n_samples_window = 1024
freq, time, stft = spectrogram(
    decimated_audio_book, fs=int(audio_book.sample_rate/factor), 
    window=get_window('hann', n_samples_window), 
    #nperseg=None, 
    noverlap=int(n_samples_window/2), nfft=n_samples_window, 
    #detrend='constant', 
    return_onesided=True, scaling='spectrum', axis=-1, mode='complex')
db_values = librosa.amplitude_to_db(np.abs(stft))

fig_handler = plt.figure(dpi= 80, facecolor='w', edgecolor='k')
specshow(db_values, sr=int(audio_book.sample_rate/factor), y_axis='linear', cmap='magma')
fig_handler.tight_layout()
plt.colorbar(format='%+2.0f dB')
plt.title('linear' + '-frequency power spectrogram')

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

Text(0.5, 1, 'linear-frequency power spectrogram')

In [27]:
iAudio(decimated_audio_book, rate=int(audio_book.sample_rate/factor))

## 6. Full signal process chain validation
Signal process chain consists in several steps:
* Load signal 
* Tone generation 4kHz and 6kHz
* Add noise tones to audio
* Resample to targeted sampling rate 11025 sps
* STFT calculation in complex mode. Complex FFT-->absolute for noise substraction
* Substract pure tone in absolute value
* Reconstruct complex from old phase and new magnitude (with substracted pure tone) and Inverse STFT

### 6.2 Noise tones generation

In [28]:
# Generating a pure tone in centered in f0 with the same rate as the noise signal
seconds_duration = 5
f_6k = 6e3
f_4k = 4e3
time_sim = np.arange(0,seconds_duration,1/audio_book.sample_rate)
tone_6k = np.sin(2*np.pi*f_6k*time_sim)
tone_4k = np.sin(2*np.pi*f_4k*time_sim)
noise_signal = 40*(tone_4k + tone_6k)

f, Pxx = scipy.signal.welch(noise_signal, fs = audio_book.sample_rate)

fig_handler = plt.figure(dpi= 80, facecolor='w', edgecolor='k')
plt.plot(f,Pxx)
fig_handler.tight_layout()
plt.title('Noise signal spectrum')

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

Text(0.5, 1, 'Noise signal spectrum')

In [29]:
n_samples_window = 1024
freq, time, stft = spectrogram(
    noise_signal, fs=int(audio_book.sample_rate), 
    window=get_window('hann', n_samples_window), 
    #nperseg=None, 
    noverlap=int(n_samples_window/2), nfft=n_samples_window, 
    #detrend='constant', 
    return_onesided=True, scaling='spectrum', axis=-1, mode='complex')
db_values = librosa.amplitude_to_db(np.abs(stft))

fig_handler = plt.figure(dpi= 80, facecolor='w', edgecolor='k')
specshow(db_values, sr=int(audio_book.sample_rate), y_axis='linear', cmap='magma')
fig_handler.tight_layout()
plt.colorbar(format='%+2.0f dB')
plt.title('linear' + '-frequency power spectrogram')

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

Text(0.5, 1, 'linear-frequency power spectrogram')

### 6.3 Add tones to audio book

In [30]:
audio_book_data = audio_book.samples
audio_book_data[0:len(noise_signal)] += noise_signal
iAudio(audio_book_data, rate=int(audio_book.sample_rate))

In [31]:
n_samples_window = 1024
freq, time, stft = spectrogram(
    audio_book_data, fs=int(audio_book.sample_rate), 
    window=get_window('hann', n_samples_window), 
    #nperseg=None, 
    noverlap=int(n_samples_window/2), nfft=n_samples_window, 
    #detrend='constant', 
    return_onesided=True, scaling='spectrum', axis=-1, mode='complex')
db_values = librosa.amplitude_to_db(np.abs(stft))

fig_handler = plt.figure(dpi= 80, facecolor='w', edgecolor='k')
specshow(db_values, sr=int(audio_book.sample_rate), y_axis='linear', cmap='magma')
fig_handler.tight_layout()
plt.colorbar(format='%+2.0f dB')
plt.title('linear' + '-frequency power spectrogram')

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

Text(0.5, 1, 'linear-frequency power spectrogram')

### 6.4 Resample to target frequency
Resampling audio to targeted frequency, will destroy noise above the new sampling rate/2 because previously to downsampling, an anti-aliasing filter is applied

In [32]:
target_sample_rate = 11025
decimated_audio_book = decimate(audio_book_data, int(audio_book.sample_rate/target_sample_rate))
iAudio(decimated_audio_book, rate=target_sample_rate)

### 6.5 STFT calculation

In [33]:
freq, time, stft = spectrogram(
    decimated_audio_book, fs=target_sample_rate, 
    window=get_window('hann', n_samples_window), 
    #nperseg=None, 
    noverlap=int(n_samples_window/2), nfft=n_samples_window, 
    #detrend='constant', 
    return_onesided=True, scaling='spectrum', axis=-1, mode='complex')
db_values = librosa.amplitude_to_db(np.abs(stft))

fig_handler = plt.figure(dpi= 80, facecolor='w', edgecolor='k')
specshow(db_values, sr=target_sample_rate, y_axis='linear', cmap='magma')
fig_handler.tight_layout()
plt.colorbar(format='%+2.0f dB')
plt.title('linear' + '-frequency power spectrogram')

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

Text(0.5, 1, 'linear-frequency power spectrogram')

### 6.6 Noise substraction

In [34]:
print('Shape of the STFT ' + str(db_values.shape) + '\n' +
      'Length of time vector ' + str(len(time)) + '\n' + 
      'Length of frequency vector ' + str(len(freq)))
idx_freq = int(f_4k/freq[1])
print('Targeted frequency index : ' + str(idx_freq))
np.set_printoptions(precision=3)
np.set_printoptions(suppress=True)
print(db_values[int(idx_freq-2):int(idx_freq+4),0:4])

audio_duration = len(decimated_audio_book)/target_sample_rate
print('Audio duration ' + str(audio_duration))
idx_time = int(len(time)*seconds_duration/audio_duration)
print('Targeted time index : ' + str(idx_time))
print(db_values[idx_freq-1:idx_freq+3,int(idx_time-2):int(idx_time+4)])

Shape of the STFT (513, 214)
Length of time vector 214
Length of frequency vector 513
Targeted frequency index : 371
[[-6.653 -6.786 -6.281 -6.703]
 [10.    10.186 10.019 10.056]
 [24.435 24.456 24.447 24.444]
 [24.674 24.644 24.677 24.668]
 [11.11  10.909 11.039 11.086]
 [-6.035 -4.896 -5.74  -5.924]]
Audio duration 10.0
Targeted time index : 107
[[ 1.642  6.261 17.308 13.22  11.492  3.472]
 [24.072 25.403 14.583 18.114 12.314  4.434]
 [25.325 25.767 17.275 16.641  4.677  7.613]
 [16.95  14.093 17.784 15.4   10.666  6.789]]


In the print above, its easy to see the power of the tone distributed in four bands for frequencies:
* idx - 1 = 16dB
* idx     = 30dB
* idx + 1 = 30dB
* idx + 2 = 17dB
These values should be substracted from starting idx to idx_time for time index

In [39]:
db_values_mod = deepcopy(db_values)
db_values_mod[idx_freq-1,:idx_time+1] -= 17
db_values_mod[idx_freq  ,:idx_time+1] -= 30
db_values_mod[idx_freq+1,:idx_time+1] -= 30
db_values_mod[idx_freq+2,:idx_time+1] -= 18

fig_handler = plt.figure(dpi= 80, facecolor='w', edgecolor='k')
specshow(db_values_mod, sr=target_sample_rate, y_axis='linear', cmap='magma')
fig_handler.tight_layout()
plt.colorbar(format='%+2.0f dB')
plt.title('linear' + '-frequency power spectrogram')

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

Text(0.5, 1, 'linear-frequency power spectrogram')

### 6.7 Reconstruct the signal
From the new modified module (dB in noise bands substracted) and old phase

In [52]:
phase = np.angle(stft)
mod   = librosa.db_to_amplitude(db_values_mod)
imag_recons_stft = mod*np.exp(1j*phase)
data_recovered = istft(imag_recons_stft, fs=target_sample_rate, 
    window=get_window('hann', n_samples_window), 
    #nperseg=None, 
    noverlap=int(n_samples_window/2), nfft=n_samples_window)
iAudio(data_recovered, rate=target_sample_rate)